In [129]:
import pandas as pd
import numpy as np
import seaborn as sns
import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, LSTM
import warnings
warnings.filterwarnings("ignore")

In [2]:
returns = pd.read_pickle("./Data/returns.pkl")
returns = returns.iloc[1:]

In [3]:
# dropping columns with all NaN
drop_columns = []

for col in returns.columns:
    if returns[col].isnull().all() == True:
        drop_columns.append(col)
        
returns.drop(columns=drop_columns, inplace=True)

In [182]:
def get_investable(t, n_rows):
    "Find stocks in investable universe at time t\
    (stocks in the S&P500 that have prices recorded for the last n_rows days)"
    
    df_investable = returns.copy(deep = True).sort_index(ascending = False)
    
    #add 1 date to get the test features in investable
    t = t + pd.DateOffset(1)
    
    #if t is now a non-trading day, advance until we reach a valid trading day
    while t not in df_investable.index:
        t = t + pd.DateOffset(1)
    
    t_index = df_investable.index.get_loc(t)
    
    #take n_rows worth of data upto time specified
    df_investable = df_investable.iloc[t_index + 1:t_index + n_rows + 1]
    
    #find all stocks that exist in the S&P at this time period
    investable_universe = []
    for col in df_investable.columns:
        if ~df_investable[col].iloc[:n_rows].isna().any():
            investable_universe.append(col)
        
    df_investable = df_investable[investable_universe]
    
    return df_investable

In [251]:
def format_investable(df, n_in=1, n_out=1):
    "Takes investable dataframe and formats it to have all stock returns at time t-1\
    (the features) and all corresponding stock returns at time t (the targets)\
    n_in is the number of past returns we want to use, n_out is the number of future \
    returns we want to predict"
    
    n_vars = df.shape[1]
    
    cols = []
    input_col_names = df.add_suffix(' (t-1)').columns
    forecast_col_names = df.add_suffix(' (t)').columns
    names = input_col_names.append(forecast_col_names)
    
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))

    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        
    # put it all together
    agg = pd.concat(cols, axis=1)
    agg.columns = names
    
    # drop the first row (it contains NaNs)
    agg.dropna(inplace=True)
    
    return agg

In [223]:
def reshape_investable(df):
    "Takes formatted investable and reshapes inputs it into 3D array [samples, timesteps, features]"
    
    # select columns ending with ' (t-1)' for features
    # and columns ending with ' (t)' for targets
    X_col = [df.columns[i] for i in range(df.shape[1]) if df.columns[i].endswith(' (t-1)')]
    y_col = [df.columns[i] for i in range(df.shape[1]) if df.columns[i].endswith(' (t)')]
    
    X_train = df[X_col].iloc[2:,:].values
    y_train = df[y_col].iloc[2:,:].values
    
    X_test = df[X_col].iloc[0:1,:].values
    y_test = df[y_col].iloc[0:1,:].values
    
    #reshape
    X_train = X_train.reshape(X_train.shape[0], 1, X_train.shape[1])
    X_test = X_test.reshape(X_test.shape[0], 1, X_test.shape[1])

    return X_train, y_train, X_test, y_test

In [255]:
def portfolio_return(df, n):
    "Takes dataframe with predicted and actual returns and outputs and what the equally-weighted\
    portfolio with n long and n short stocks would have actually earned"
    pred = df.sort_values(by = 'pred return', ascending = False)
    topn_p = pred.head(n)
    botn_p = pred.tail(n)
    return_a = topn_p['actual return'].sum() - botn_p['actual return'].sum()
    
    return return_a

In [307]:
def LSTM_pipeline(n_stocks, lookback):
    #dataframe to collect portfolio returns at all t
    all_returns = pd.DataFrame(columns = ['date', 'portfolio return'])
    
    date_range = returns.index[2527:]
    
    all_returns['date'] = date_range
    all_returns['date'] = all_returns['date'].astype('datetime64[ns]')
    all_returns.set_index('date', inplace = True)
    
    for t in date_range:
        t = pd.to_datetime(t)
        
        #get investable
        investable = get_investable(t, lookback)
        #format as features and targets
        f_investable = format_investable(investable)
        #get train, test sets
        X_train, y_train, X_test, y_test = reshape_investable(f_investable)

        #create model
        model = Sequential()
        model.add(LSTM(50, input_shape=(X_train.shape[1], X_train.shape[2])))
        model.add(Dense(y_train.shape[1]))

        #compile and fit model
        model.compile(loss = 'mae', optimizer = 'adam')
        history = model.fit(X_train, y_train, epochs=150, batch_size=16)

        #predict
        yhat = model.predict(X_test, verbose = 0)

        #format predictions and actual returns in dataframe
        col = [f_investable.columns[i] for i in range(f_investable.shape[1]) if f_investable.columns[i].endswith(' (t)')]
        df = pd.DataFrame(index = col, data = yhat.T)
        df = df.rename(columns = {0: 'pred return'})
        df['actual return'] = y_test.T

        #calculate portfolio return
        return_t = portfolio_return(df, 5)

        #add return to dataframe
        all_returns.loc[t]['portfolio return'] = return_t
    
    return all_returns

In [ ]:
df = LSTM_pipeline(5, 504)

Epoch 1/150
32/32 [==============================] - 2s 2ms/step - loss: 1.9938
Epoch 2/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9739
Epoch 3/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9622
Epoch 4/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9692
Epoch 5/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9006
Epoch 6/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8917
Epoch 7/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8580
Epoch 8/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8249
Epoch 9/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8139
Epoch 10/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7865
Epoch 11/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7808
Epoch 12/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7824
Epoch 13/150
32/32 [=================

32/32 [==============================] - 0s 2ms/step - loss: 1.5736
Epoch 103/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5891
Epoch 104/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5706
Epoch 105/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5472
Epoch 106/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5483
Epoch 107/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5750
Epoch 108/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5484
Epoch 109/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5379
Epoch 110/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5495
Epoch 111/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5723
Epoch 112/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5369
Epoch 113/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5441
Epoch 114/150
32/32 [=========

32/32 [==============================] - 0s 2ms/step - loss: 1.6001
Epoch 53/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6102
Epoch 54/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5863
Epoch 55/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6092
Epoch 56/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6151
Epoch 57/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6017
Epoch 58/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6083
Epoch 59/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5756
Epoch 60/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5846
Epoch 61/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5951
Epoch 62/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5925
Epoch 63/150
32/32 [==============================] - 0s 2ms/step - loss: 1.6002
Epoch 64/150
32/32 [=====================

32/32 [==============================] - 0s 2ms/step - loss: 1.9379
Epoch 3/150
32/32 [==============================] - 0s 2ms/step - loss: 2.0369
Epoch 4/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9462
Epoch 5/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8745
Epoch 6/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8652
Epoch 7/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8169
Epoch 8/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8244
Epoch 9/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8356
Epoch 10/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7912
Epoch 11/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7972
Epoch 12/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7636
Epoch 13/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7539
Epoch 14/150
32/32 [============================

32/32 [==============================] - 0s 2ms/step - loss: 1.5545
Epoch 104/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5570
Epoch 105/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5586
Epoch 106/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5658
Epoch 107/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5719
Epoch 108/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5649
Epoch 109/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5458
Epoch 110/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5780
Epoch 111/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5695
Epoch 112/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5740
Epoch 113/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5384
Epoch 114/150
32/32 [==============================] - 0s 2ms/step - loss: 1.5724
Epoch 115/150
32/32 [=========

...

32/32 [==============================] - 0s 2ms/step - loss: 1.8759
Epoch 52/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8508
Epoch 53/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8620
Epoch 54/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9093
Epoch 55/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8749
Epoch 56/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8489
Epoch 57/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8652
Epoch 58/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8718
Epoch 59/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8632
Epoch 60/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8772
Epoch 61/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8666
Epoch 62/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8468
Epoch 63/150
32/32 [=====================

32/32 [==============================] - 2s 2ms/step - loss: 2.3660
Epoch 2/150
32/32 [==============================] - 0s 2ms/step - loss: 2.3047
Epoch 3/150
32/32 [==============================] - 0s 2ms/step - loss: 2.3443
Epoch 4/150
32/32 [==============================] - 0s 2ms/step - loss: 2.3729
Epoch 5/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2813
Epoch 6/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2425
Epoch 7/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2453
Epoch 8/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1706
Epoch 9/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1732
Epoch 10/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1796
Epoch 11/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1529
Epoch 12/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1338
Epoch 13/150
32/32 [=============================

32/32 [==============================] - 0s 2ms/step - loss: 1.8261
Epoch 103/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8330
Epoch 104/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8503
Epoch 105/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8380
Epoch 106/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7995
Epoch 107/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8080
Epoch 108/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8190
Epoch 109/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7907
Epoch 110/150
32/32 [==============================] - 0s 2ms/step - loss: 1.7994
Epoch 111/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8020
Epoch 112/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8346
Epoch 113/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8085
Epoch 114/150
32/32 [=========

32/32 [==============================] - 0s 2ms/step - loss: 1.8849
Epoch 53/150
32/32 [==============================] - 0s 1ms/step - loss: 1.8799
Epoch 54/150
32/32 [==============================] - 0s 1ms/step - loss: 1.8761
Epoch 55/150
32/32 [==============================] - 0s 1ms/step - loss: 1.9039
Epoch 56/150
32/32 [==============================] - 0s 1ms/step - loss: 1.8603
Epoch 57/150
32/32 [==============================] - 0s 1ms/step - loss: 1.8668
Epoch 58/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8711
Epoch 59/150
32/32 [==============================] - 0s 1ms/step - loss: 1.8624
Epoch 60/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8938
Epoch 61/150
32/32 [==============================] - 0s 2ms/step - loss: 1.9194
Epoch 62/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8530
Epoch 63/150
32/32 [==============================] - 0s 2ms/step - loss: 1.8879
Epoch 64/150
32/32 [=====================

32/32 [==============================] - 0s 2ms/step - loss: 2.3544
Epoch 3/150
32/32 [==============================] - 0s 2ms/step - loss: 2.3526
Epoch 4/150
32/32 [==============================] - 0s 2ms/step - loss: 2.3051
Epoch 5/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2750
Epoch 6/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2685
Epoch 7/150
32/32 [==============================] - 0s 2ms/step - loss: 2.2782
Epoch 8/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1845
Epoch 9/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1677
Epoch 10/150
32/32 [==============================] - 0s 1ms/step - loss: 2.1660
Epoch 11/150
32/32 [==============================] - 0s 2ms/step - loss: 2.1174
Epoch 12/150
32/32 [==============================] - 0s 2ms/step - loss: 2.0968
Epoch 13/150
32/32 [==============================] - 0s 2ms/step - loss: 2.0925
Epoch 14/150
32/32 [============================